# препроцессинг русcкоязычных текстов

In [7]:
# загрузка пакетов
import csv
import pymystem3
import re

Нужно указать каталог в котором лежит файл с текстами и тип загрузки, то ест кодировку и разделитель
### Обратите внимание что пакет pymystem3 должен быть установлен

In [8]:
INPUT_FILE = 'C:/Users/Koltcov/Jupiter_lessons/koltsov_course/etnic_test.csv'
TEXT_FIELD = 0

in_data = csv.reader(open(INPUT_FILE, encoding='utf8', newline=''), delimiter=';')


в файле etnic_test.csv содержится набор текстов и тональных оценок. И хотя для данного урока оценки нам не нужны, 
они понадобятся потом при рассмотрении темы ‘Sentiment analysis’. Так что сделаем код на будущее.

In [18]:
empty = 0

# тут будет хранится список оригинальных текстов
x_data = []
# тут будет хранится список лематизированных текстов
y_data = []
# тут будет храится список ответов
z_data = []

# создание объекта mystem
m = pymystem3.Mystem()



for i, line in enumerate(in_data):
     text = str(line[TEXT_FIELD:])
     s = text.replace('"', '')
     s = m.lemmatize(s)
     s = ''.join(s)
     lemans=str(s)

     lemans = re.sub('[!@#$1234567890#]', '', lemans)

     #print(''.join(lemmas))

     x_data.append(text)
     y_data.append(lemans)
     z_data.append(line[TEXT_FIELD +1:])

     print('doc:' , i)
     #print('тональная оценка: ', z_data[i])
     #print('лематизированный текст: ', y_data[i])
     #if i > 5: break
    
print('Загрузка данных и процедура лематизации завершена')

doc: 0
doc: 1
doc: 2
doc: 3
doc: 4
doc: 5
doc: 6
doc: 7
doc: 8
doc: 9
doc: 10
doc: 11
doc: 12
doc: 13
doc: 14
doc: 15
doc: 16
doc: 17
doc: 18
doc: 19
doc: 20
doc: 21
doc: 22
doc: 23
doc: 24
doc: 25
doc: 26
doc: 27
doc: 28
doc: 29
doc: 30
doc: 31
doc: 32
doc: 33
doc: 34
doc: 35
doc: 36
doc: 37
doc: 38
doc: 39
doc: 40
doc: 41
doc: 42
doc: 43
doc: 44
doc: 45
doc: 46
doc: 47
doc: 48
Загрузка данных и процедура лематизации завершена


Теперь, нужно сформировать  список стоп слов, которые нужно удалять в дальнейшем. 
Списки стоп слов можно формировать как на основе частот, так и на основе величин tf-idf.
Однако ,если расчет tf-idf уже реализован в виде готовой процедуры (покажем чуть позже), то подсчет абсолютных частот слов не реализован. Но его можно очень просто реализовать.
Код ниже демонстрирует как это сделать. 


Однако, прежде чем запихивать в это  код большое количество текстов, разберем как код работает на нескольких простых текстах.

In [19]:
import numpy as np
print('запускаем векторизации')
from sklearn.feature_extraction.text import CountVectorizer
# Convert a collection of text documents to a matrix of token counts
vec = CountVectorizer()

запускаем векторизации


np - это бабиотека, которая предоставляет удобный интерфейс по работе с массивами.
sklearn - библиотека, в которой реализованно большое количество алгоритмов машинного обучения
feature_extraction - процедура выделения фич из текстов. Собственно данная процедура конвертирует коллецию текстов в матрицу ,в которой хрантся абсолютные частоты слов. 

В нашем примере, массив y_data содержит лематизированные тексты

In [20]:
# test example
y_data1=('"Это моя книга"','Книга ужасна',' моя история закончена')

x = vec.fit_transform(y_data1)
data = vec.fit_transform(y_data1).toarray()

num_docs, num_feature =x.shape
print('число документов: ', num_docs, 'число фич: ', num_feature)

число документов:  3 число фич:  6


Матрица data = vec.fit_transform(y_data).toarray() содержит частоты слов.
В данной матрице каждая сторока это документ, число колонок это число уникальных слов-фич в коллекции
команда num_docs, num_feature =x.shape - позволяет узнать нам сколько у нас документов (то есть строк) и сколько колонок (то есть фич)
Давайте посмотрим какие слова-фичи у нас получились.

In [21]:
# получаем список фич
myfich=vec.get_feature_names()

print('Фича под номеров 2:', myfich[1])
# внимание нумерация фич начинается с нуля
print('Полный список фич')
print(myfich)

Фича под номеров 2: история
Полный список фич
['закончена', 'история', 'книга', 'моя', 'ужасна', 'это']


In [ ]:
Теперь давайте посмотрим как выглядит матрица 'data' второго по счету документа

In [22]:
print(data[:1])

[[0 0 1 1 0 1]]


In [23]:
# полная матрица data
print(data)


[[0 0 1 1 0 1]
 [0 0 1 0 1 0]
 [1 1 0 1 0 0]]


Итак, у нас три документа (три строки) и шесть фич-слов (шесть колонок). Содержимое каждой ячейки это частота конкретной фичи в конкретном документе. Например, Первая строка имеет вид 0 0 1 1 0 1, что означает
'закончена' - частота = 0
'история'- частота = 0
'книга'- частота = 1 
'моя' - частота = 1 
'ужасна' - частота = 0
'это' - частота = 1
то есть у нас вот такой документ:
'книга' + 'моя' + 'это' = "Это моя книга"

### Таким образом ,что бы посчитать частоты слов нужно сложить все строки по колонкам. 

In [24]:
# склдаываем строки
# суммирование частот фич по всем документам
freq_data = data.sum(axis=0)
print(freq_data)

[1 1 2 2 1 1]


Таким образом, в нашей коллекции из трех документов
('"Это моя книга"','Книга ужасна',' моя история закончена')
частоты слов следующие
'закончена' - частота в коллкции = 1
'история'- - частота в коллкции = 1
'книга'- - частота в коллкции = 2
'моя' -- частота в коллкции = 2
'ужасна' - - частота в коллкции = 1
'это' - - частота в коллкции = 1

### Теперь подсчитаем частоты фич в большой коллкции, которая хранится в y_data

In [25]:
x = vec.fit_transform(y_data)
data = vec.fit_transform(y_data).toarray()

num_docs, num_feature =x.shape
print('число документов: ', num_docs, 'число фич: ', num_feature)

число документов:  49 число фич:  1461


In [42]:
# получаем список фич
myfich=vec.get_feature_names()

print('Фича под номеров 2:', myfich[1])
# внимание нумерация фич начинается с нуля
print('Полный список фич')
print(myfich)

Фича под номеров 2: _blank
Полный список фич
['_all_nopic', '_blank', '_utl_tmr', '_www', 'amerikanskiy', 'anghel', 'articles', 'articles_content', 'avagyan', 'ba', 'bb', 'bf', 'bismark', 'blog', 'blogs', 'boardjob', 'cat', 'cc', 'changeip', 'chechency', 'cid', 'city', 'cler', 'club', 'content', 'ddeec', 'dengi', 'discovery', 'domainmirtesen', 'donbass', 'dsrgbjmhc', 'dyatlova', 'ec', 'ee', 'ekonomika', 'ekozyanc', 'estonii', 'ezafezep', 'fa', 'faktyi', 'fbe', 'fe', 'filipp', 'fo', 'fon', 'full', 'gastarbayterov', 'ge', 'gh', 'godu', 'gosudarstvo', 'gulag', 'hram', 'hronika', 'html', 'http', 'https', 'id', 'image', 'info', 'infocafe', 'infopolk', 'ip', 'izbaloval', 'izvestia', 'jar', 'kazachja_mysl', 'kazk', 'kieve', 'kiwix', 'komandir_batalona_donbass_dal_ocenku_armii_putina', 'konopljov', 'korolkov', 'kotoryie', 'kramtp', 'krasvremya', 'krichim', 'ksu', 'kz', 'levashov', 'li', 'library', 'licu', 'livejournal', 'load', 'madalin', 'majdan', 'maxpark', 'me', 'media', 'mezhdunarodnaya', 

In [26]:
# склдаываем строки
# суммирование частот фич по всем документам
freq_data = data.sum(axis=0)
print(freq_data)

[ 2 54  2 ...,  1  2  1]


In [27]:
# сохраняем список фич и их частот в текстовый файл формата csv
# сохранение списка фич и частоты фич в текстовый файл
f = open('C:/Users/Koltcov/Jupiter_lessons/koltsov_course/freq_words.csv', 'w')
for i, line in enumerate(myfich):
     #print(myfich[i], ' ; ', freq_data[i])
     ss = myfich[i] + ';' + str(freq_data[i])
     f.write(ss + '\n')

f.close()
print('создание списка фич и частот завершено')

создание списка фич и частот завершено


# Удаление стоп слов из коллкции текстов.
несмотря на то что CountVectorizer или TfidfVectorizer содержит встроенные списки стоп слов для русского языка. 
Все же рекомендуется создавать свои собственные списки стоп слов, релевантные для конкретной коллекции.
Для особо ленивых можно пойти вот сюда и скачать списки стоп слов.
примеры список стоп слов: https://github.com/stopwords-iso/stopwords-ru/tree/master/raw
Рассмотрим как можно удалить стоп слова из коллекции лемматизирвоанных текстов, при условии что имеется файл со стоп словами.

In [28]:
# определяем имя файла cо списоком стоп слов 
file_name='C:/Users\Koltcov/Jupiter_lessons/koltsov_course/my_stop.txt'
# создаем список
words = []

# читаем в это список слова из  файла
for line in open(file_name):
    line = line.split('\n') # из строки получаем список
    line = line[0]
    words.append(line)

words = frozenset(words)

print('процесс векторизации')
from sklearn.feature_extraction.text import TfidfVectorizer
vec = TfidfVectorizer(ngram_range=(1,1),stop_words=(words))

процесс векторизации


ngram_range - параметр определяющий размер n-граммы, например 2 означает что будут также расчитыватся биграммы в ходе процедуры векторизации текстов.

In [29]:
x = vec.fit_transform(y_data)
data = vec.fit_transform(y_data).toarray()

num_docs, num_feature =x.shape
print('число документов: ', num_docs, 'число фич: ', num_feature)

число документов:  49 число фич:  1296


### обратите внимание ,что до удаления стоп слов, у нас число фич было 1324, а теперь стало 1168
таким образом, удаление стоп слов позволяет существенно снизить размерность матрицы, которая в бальнейшем будет использоватся. 
Однако, если увеличить размер парметра ngram_range, то мы снова увеличим размерность пространства фич, так как в этом случае получим еще и список биграм.

In [49]:
vec = TfidfVectorizer(ngram_range=(1,2),stop_words=(words))
x = vec.fit_transform(y_data)
data = vec.fit_transform(y_data).toarray()

num_docs, num_feature =x.shape
print('число документов: ', num_docs, 'число фич: ', num_feature)

число документов:  44 число фич:  2701


# Задание на дом №1
Установить Anaconda, установить необходмые пакеты, включая pymystem3.
Описание pymystem3 можно найти вот тут:https://pypi.python.org/pypi/pymystem3/0.1.1

# Задание на дом №2
нужно загрузить полную коллекцию этнически окрашенных текстов, получить для нее список фич и частот. Далее, построить список стоп слов на основании полученного частотного списка. Далее, посчитить коллкцию текстов и расчитать количество фич при ngram_range=1

In [ ]:
# загрузить коллекцию можно по адресу: https://yadi.sk/d/P2YAscXx3S3GU5

In [ ]:
При возникновении вопрос писать по адресам
Кольцов С.Н: kol-sergei@yandex.ru
Нагорный О.: nagornyy.o@gmail.com